In [1]:
# Import modules
import folium
import os
import requests
import json
import pandas
from pandas.io.json import json_normalize
import numpy
import geopandas
import descartes
import pickle
import branca
from branca.colormap import linear
from folium.plugins import Search
from ibge.localidades import *
# Set ipython's max row display
pandas.set_option('display.max_row', 100)
# Set iPython's max column width to 50
pandas.set_option('display.max_columns', 50)

In [2]:
## Regioes
data = Regioes()

In [3]:
#### count() - number datatype
data.count()

5

In [4]:
## Estados
data = Estados()

In [5]:
#### count() - number datatype
data.count()

27

In [6]:
## Municípios
data = Municipios()


##  Criando um mapa com contornos

In [7]:
# url to request information of all Federative Units in Brazil (contains the id number)
states_url = 'https://servicodados.ibge.gov.br/api/v1/localidades/estados'

# requesting informations and assigning the a variable
states_data = requests.get(states_url, headers=headers).json()

In [8]:
# url to request information of all Federative Units in Brazil (contains the id number)
muni_url = 'https://servicodados.ibge.gov.br/api/v1/localidades/municipios'

# requesting informations and assigning the a variable
cities_data = requests.get(muni_url, headers=headers).json()


In [9]:
# Resulution
## 0. Nenhuma divisão político-administrativa é inserida no interior da malha
## 1. Inclui na malha as macrorregiões. Válido apenas quando a localidade for BR.
## 2. Inclui na malha as Unidades da Federação. Válido apenas quando a localidade for BR ou uma macroregião
## 3. Inclui na malha as mesorregiões. Válido apenas quando a localidade for BR, macroregião ou Unidade da Federação
## 4. Inclui na malha as microrregiões. Válido apenas quando a localidade for BR, macroregião, Unidade da Federação ou mesorregião
## 5. Inclui na malha os municípios
meshes_url1 = 'https://servicodados.ibge.gov.br/api/v2/malhas/?resolucao=1&formato=application/vnd.geo+json'
meshes_url2 = 'https://servicodados.ibge.gov.br/api/v2/malhas/?resolucao=2&formato=application/vnd.geo+json'
meshes_url3 = 'https://servicodados.ibge.gov.br/api/v2/malhas/?resolucao=3&formato=application/vnd.geo+json'
meshes_url4 = 'https://servicodados.ibge.gov.br/api/v2/malhas/?resolucao=4&formato=application/vnd.geo+json'
meshes_url5 = 'https://servicodados.ibge.gov.br/api/v2/malhas/?resolucao=5&formato=application/vnd.geo+json&qualidade=4'
# requesting geojson data and assigning to a variable
meshes_macro = requests.get(meshes_url1, headers=headers).json()
meshes_ufs = requests.get(meshes_url2, headers=headers).json()
meshes_meso = requests.get(meshes_url3, headers=headers).json()
meshes_micro = requests.get(meshes_url4, headers=headers).json()
meshes_mun = requests.get(meshes_url5, headers=headers).json()

## Leitura de campos do arquivo JSON




In [10]:
# Obtendo o código IBGE de cada área.
for mun in meshes_mun['features']: 
  codarea   = mun['properties']['codarea']
  centroide = mun['properties']['centroide']
  #print(codarea)
  print("Codearea = " + str(codarea) + " ***  Centroide = " + str(centroide))


Codearea = 5007901 ***  Centroide = [-54.94234709013311, -21.093444963516493]
Codearea = 5007935 ***  Centroide = [-54.43679927519888, -17.64612094496461]
Codearea = 5007950 ***  Centroide = [-54.99060087144322, -23.648986359593817]
Codearea = 5007976 ***  Centroide = [-53.43077423505117, -22.66971121145116]
Codearea = 5008008 ***  Centroide = [-55.02465958217724, -20.44672000286447]
Codearea = 5008305 ***  Centroide = [-52.21123035176926, -20.4385944588137]
Codearea = 5008404 ***  Centroide = [-54.42427374484512, -22.46735870053217]
Codearea = 5001003 ***  Centroide = [-51.29044123023306, -20.075976997574337]
Codearea = 5006309 ***  Centroide = [-51.395296399612334, -19.52757463914529]
Codearea = 5007802 ***  Centroide = [-51.75726065199317, -20.2823868540638]
Codearea = 5201504 ***  Centroide = [-52.04564444334576, -18.76783675713795]
Codearea = 5201702 ***  Centroide = [-52.1468663901787, -15.970150495669516]
Codearea = 5203104 ***  Centroide = [-52.43802923762304, -16.360548844328

## Fusão de dados: indicadores municipais ao arquivo de malhas GeoJson


In [11]:
for mun in meshes_mun["features"]:
    codarea = int(mun["properties"]["codarea"])
    matched_city = [city for city in cities_data if city["id"] == codarea][0]
    mun["properties"]["nome"] = matched_city["nome"] 

In [12]:
# meshes_mun['features']

In [13]:
indicadores_mun = pandas.read_json(r'/Users/marcelino/jota_eleitoral/data/indicadores_municipais.json', orient='records')

indicadores_mun['id'] = indicadores_mun['id'].astype(int)
indicadores_mun['codigo_tse'] = indicadores_mun['codigo_tse'].astype(int)

indicadores_mun.info()




<class 'pandas.core.frame.DataFrame'>
RangeIndex: 5570 entries, 0 to 5569
Data columns (total 37 columns):
 #   Column                       Non-Null Count  Dtype  
---  ------                       --------------  -----  
 0   id                           5570 non-null   int64  
 1   nome                         5570 non-null   object 
 2   lat                          5570 non-null   float64
 3   lng                          5570 non-null   float64
 4   codigo_tse                   5570 non-null   int64  
 5   capital                      5570 non-null   int64  
 6   qtd_eleitores                5568 non-null   float64
 7   qtd_eleitores_feminino       5568 non-null   float64
 8   qtd_eleitores_masculino      5568 non-null   float64
 9   qtd_eleitores_16             5568 non-null   float64
 10  qtd_eleitores_17             5568 non-null   float64
 11  qtd_eleitores_18             5568 non-null   float64
 12  qtd_eleitores_19             5568 non-null   float64
 13  qtd_eleitores_20  

In [14]:
# Merging Dataframes

# creating lists to be populated by IBGE requested data
meshes_ids = []
states_ids = []
states_names = []
states_codes = []

# populating information about meshes
for feature in meshes_ufs['features']:
    meshes_ids.append( str(feature['properties']['codarea']) )

meshes_ids.sort()

# populating information about Federative Units
for state in states_data:
    states_ids.append( str(state['id']) )
    states_names.append( state['nome'] )
    states_codes.append( state['sigla'] )

states_ids.sort()

# checking if identification numbers matches
meshes_ids == states_ids

True

In [15]:
# creating a dataframe of Federative Units to be merged
states = pandas.DataFrame( {'id': states_ids, 'nome': states_names, 'sigla': states_codes} )

# appending centroid coordinates columns
states['lat'] = 0
states['lng'] = 0

states.set_index('id', inplace=True)

# retrieving centroid data
for feature in meshes_ufs['features']:
    
    centroid = feature['properties']['centroide']
    lat = centroid[1]
    lng = centroid[0]
    
    cod = str(feature['properties']['codarea'])
    
    states.loc[cod,'lat'] = lat
    states.loc[cod,'lng'] = lng

states.reset_index(inplace=True)

states.head()

id      nome sigla        lat        lng
0  11  Rondônia    RO -10.913325 -62.841698
1  12      Acre    AC  -9.212917 -70.473083
2  13  Amazonas    AM  -4.154223 -64.653187
3  14   Roraima    RR   2.084090 -61.399162
4  15      Pará    PA  -3.974815 -53.064197

## Desenhando com os dados
               

In [16]:
## auxiliary finctions


highlight_function = lambda x: {'fillColor': '#000000', 
                                'color':'#000000', 
                                'fillOpacity': 0.25, 
                                'weight': 0.1}


In [17]:

map_dict = indicadores_mun.set_index('id')['pop2019'].to_dict()

color_scale = branca.colormap.LinearColormap(['yellow', 'orange', 'brown'], vmin = min(map_dict.values()), vmax = max(map_dict.values())).to_step(100)


def get_color(feature):
    value = map_dict.get(feature['properties']['codarea'])
    if value is None:
        return '#8c8c8c' # MISSING -> gray
    else:
        return color_scale(value)



colorscale_pop = branca.colormap.LinearColormap(['yellow', 'orange', 'brown'], vmin = min(map_dict.values()), vmax = max(map_dict.values())).to_step(100)


# colorscale_pop = branca.colormap.linear.YlOrRd_09.scale(0, 50e3)

pop_series_dict = cities.set_index('id')['pop2019']


pop_style_function = lambda feature: {
        'fillColor': get_color(feature),
        'color': 'gray',
        'weight': 0.1,
        'fillOpacity': 0.5,
    }



NameError: name 'cities' is not defined

In [140]:

colormap = branca.colormap.linear.YlOrRd_09.scale(
    cities.pop2019.min(),
    cities.pop2019.max())


leg_brks = list(cities[cities.index.isin([780, 2500, 5000, 10000, 50000, 100000, 1000000, 12252024])]['pop2019'])

leg_brks.append(0)

leg_brks.sort()

leg_brks


colormap = colormap.to_step(n=100, quantiles=leg_brks)

colormap

In [154]:
# coordinations of Federal District
federal_district = [-15.7757875,-48.0778477]



# creating the map object
basemap = folium.Map(
    location=federal_district,
    zoom_start=5,
    min_zoom=4,
    scrollWheelZoom=False,
    tiles='cartodbpositron'
)



cidadegeo = folium.features.GeoJson(
    data=meshes_mun,
    smooth_factor=2,
    name='população: 2019',
    #control=False, # desabilita o controle do layer no menu
    show=True,
    style_function=pop_style_function,  
    highlight_function=highlight_function,
    tooltip=folium.features.GeoJsonTooltip(
    fields=['nome','codarea'],
    aliases=['Mun: ','Pop: '],
    style=("background-color: white; color: #333333; font-family: roboto; font-size: 12px; padding: 10px;"),
    sticky=True,
    labels=True,
    toLocaleString=True,
    localize=True)
    ).add_to(basemap)


citysearch = Search(
    layer=cidadegeo,
    geom_type='Point',
    placeholder='Busca por cidade',
    collapsed=True,
    search_label='nome'
).add_to(basemap)



folium.LayerControl(collapsed=False).add_to(basemap)
# colormap = colormap.to_step(index=cut_bins)
# color_scale.add_to(basemap)
# colormap.add_to(basemap)
basemap


In [155]:

basemap.save('docs/2020.html')

basemap.save('docs/index.html')


In [ ]:
url = 'https://raw.githubusercontent.com/betafcc/Municipios-Brasileiros-TSE/master/municipios_brasileiros_tse.csv'

mun_data = pandas.read_csv(url)

indicadores_mun['id'] = indicadores_mun['id'].astype(int)
indicadores_mun['codigo_tse'] = indicadores_mun['codigo_tse'].astype(int)

indicadores_mun.info()


In [ ]:
# TSE
for mun in meshes_mun["features"]:
    codarea = int(mun["properties"]["codarea"])
    matched_city = [city for city in indicadores_mun if city["codigo_ibge"] == codarea][0]
    mun["properties"]["codigo_tse"] = matched_city["codigo_tse"]



# Eleitores
for mun in meshes_mun["features"]:
    codarea = int(mun["properties"]["codarea"])
    matched_city = [city for city in tse_data if city["id"] == codarea][0]
    mun["properties"]["qtd_eleitores"] = matched_city["qtd_eleitores"]


# Eleitores
for mun in meshes_mun["features"]:
    codarea = int(mun["properties"]["codarea"])
    matched_city = [city for city in indicadores_mun if city["id"] == codarea][0]
    mun["properties"]["pct_eleitores_feminino"] = matched_city["pct_eleitores_feminino"] 

# Eleitores
for mun in meshes_mun["features"]:
    codarea = int(mun["properties"]["codarea"])
    matched_city = [city for city in indicadores_mun if city["id"] == codarea][0]
    mun["properties"]["pct_eleitores_60a100"] = matched_city["pct_eleitores_60a100"] 


# Eleitores
for mun in meshes_mun["features"]:
    codarea = int(mun["properties"]["codarea"])
    matched_city = [city for city in indicadores_mun if city["id"] == codarea][0]
    mun["properties"]["pct_biometria"] = matched_city["pct_biometria"] 


# Intervalos 
 bins = list(cities['pop2019'].quantile([0, 0.1, 0.2, 0.3,0.5,0.6,0.7,0.8,0.9, 1]))
# threshold_scale = numpy.linspace(cities['pop2019'].min(), cities['pop2019'].max(), 6, dtype=int) 
# threshold_scale = threshold_scale.tolist()

cut_bins = [cities['pop2019'].min()-1, 2500, 5000, 10000, 50000, 100000, 1000000, cities['pop2019'].max()+1] 



cities['pop_quantile'] = pandas.qcut(cities['pop2019'], q=4)

cities['pop_quintiles'] = pandas.qcut(cities['pop2019'], q=5)

cities['pop_deciles'] = pandas.qcut(cities['pop2019'], q=10)

cut_labels_4 = ['muito pequena', 'pequena', 'media baixa', 'media', 'media alta', 'alta', 'muito alta']

cities['pop_int'] = pandas.cut(cities['pop2019'], bins=cut_bins)

cities['pop_int_lbs'] = pandas.cut(cities['pop2019'], bins=cut_bins, labels=cut_labels_4)

cities.head()






colormap = branca.colormap.linear.YlOrRd_09.scale(
    cities.pop2019.min(),
    cities.pop2019.max())

print(colormap(5.0))

colormap


colormap = colormap.to_step(index=[780, 2500, 5000, 10000, 50000, 100000, 1000000, 12252024])


pop_style_function2=lambda feature: {
        'fillColor': colormap(pop_series_dict[feature['properties']['codarea']]),
        'weight':0,
        'fillOpacity': 0.8,
    }



